# Getting started

The `xdatasets` library enables users to effortlessly access a vast collection of earth observation datasets that are compatible with `xarray` formats.

The library adopts an opinionated approach to data querying and caters to the specific needs of certain user groups, such as hydrologists, climate scientists, and engineers. One of the functionalities of `xdatasets` is the ability to extract data at a specific location or within a designated region, such as a watershed or municipality, while also enabling spatial and temporal operations.

To use `xdatasets`, users must employ a query. For instance, a straightforward query to extract the variables `t2m` (*2m temperature*) and `tp` (*Total precipitation*) from the `era5_reanalysis_single_levels` dataset at two geographical positions (Montreal and Toronto) could be as follows:

```python
query = {
    "datasets": {"era5_reanalysis_single_levels_dev": {'variables': ["t2m", "tp"]}},
    "space": {
        "clip": "point", # bbox, point or polygon
        "geometry": {'Montreal' : (45.508888, -73.561668),
                     'Toronto' : (43.651070, -79.347015)
                    }
    }
}
```

An example of a more complex query would look like the one below. 

> **Note**
> Don't worry! Below, you'll find additional examples that will assist in understanding each parameter in the query, as well as the possible combinations.

This query calls the same variables as above. However, instead of specifying geographical positions, a GeoPandas.DataFrame is used to provide features (such as shapefiles or geojson) for extracting data within each of them. Each polygon is identified using the unique identifier `Station`, and a spatial average is computed within each one `(aggregation: True)`. The dataset, initially at an hourly time step, is converted into a daily time step while applying one or more temporal aggregations for each variable as prescribed in the query. `xdatasets` ultimately returns the dataset for the specified date range and time zone.

```python
query = {
    "datasets": {"era5_reanalysis_single_levels_dev": {'variables': ["t2m", "tp"]}},
    "space": {
        "clip": "polygon", # bbox, point or polygon
        "aggregation": True, # spatial average of the variables within each polygon
        "geometry": gdf,
        "unique_id": "Station" # unique column name in geodataframe
    },
    "time": {
        "timestep": "D",
        "aggregation": {"tp": np.nansum, 
                        "t2m": [np.nanmax, np.nanmin]},
        
        "start": '2000-01-01',
        "end": '2020-05-31',
        "timezone": 'America/Montreal',
    },
}
```




## Query climate datasets

In order to use `xdatasets`, you must import at least `xdatasets`, `pandas`, `geopandas`, and `numpy`. Additionally, we import `pathlib` to interact with files.

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os

os.environ["USE_PYGEOS"] = "0"
from pathlib import Path

import geopandas as gpd

# Visualization
import hvplot.pandas  # noqa
import hvplot.xarray  # noqa-
import numpy as np
import pandas as pd
import panel as pn  # noqa

import xdatasets as xd

/home/runner/micromamba/envs/xdatasets/lib/python3.9/site-packages/clisops/core/regrid.py:42: UserWarning: xarray version >= 2023.03.0 is not supported for regridding operations with cf-time indexed arrays. Please use xarray version < 2023.03.0. For more information, see: https://github.com/pydata/xarray/issues/7794.
  warnings.warn(


### Clip by points (sites)


To begin with, we need to create a dictionary of sites and their corresponding geographical coordinates.

In [3]:
sites = {
    "Montreal": (45.508888, -73.561668),
    "New York": (40.730610, -73.935242),
    "Miami": (25.761681, -80.191788),
}

We will then extract the `tp` (*total precipitation*) and `t2m` (*2m temperature*) from the `era5_reanalysis_single_levels` dataset for the designated sites. Afterward, we will convert the time step to daily and adjust the timezone to Eastern Time. Finally, we will limit the temporal interval.

Before proceeding with this first query, let's quickly outline the role of each parameter:

- **datasets**: A dictionary where datasets serve as keys and desired variables as values.
- **space**: A dictionary that defines the necessary spatial operations to apply on user-supplied geographic features.
- **time**: A dictionary that defines the necessary temporal operations to apply on the datasets

For more information on each parameter, consult the API documentation.

This is what the requested query looks like :

In [4]:
query = {
    "datasets": "era5_reanalysis_single_levels",
    "space": {"clip": "point", "geometry": sites},  # bbox, point or polygon
    "time": {
        "timestep": "D",  # http://pandas.pydata.org/pandas-docs/stable/user_guide/timeseries.html#offset-aliases
        "aggregation": {"tp": np.nansum, "t2m": np.nanmean},
        "start": "1959-01-01",
        "timezone": "America/Montreal",
    },
}
xds = xd.Query(**query)

  0%|          | 0/2 [00:00<?, ?it/s]

Temporal operations: processing t2m with era5_reanalysis_single_levels:   0%|          | 0/2 [00:00<?, ?it/s]

Temporal operations: processing t2m with era5_reanalysis_single_levels:  50%|█████     | 1/2 [00:02<00:02,  2.90s/it]

Temporal operations: processing tp with era5_reanalysis_single_levels:  50%|█████     | 1/2 [00:02<00:02,  2.90s/it] 

Temporal operations: processing tp with era5_reanalysis_single_levels: 100%|██████████| 2/2 [00:05<00:00,  2.45s/it]

Temporal operations: processing tp with era5_reanalysis_single_levels: 100%|██████████| 2/2 [00:05<00:00,  2.52s/it]

By accessing the `data` attribute, you can view the data obtained from the query. It's worth noting that the variable name `tp` has been updated to `tp_nansum` to reflect the reduction operation (`np.nansum`) that was utilized to convert the time step from hourly to daily. Likewise, `t2m` was updated to `t2m_nanmean`. 

In [5]:
xds.data

<xarray.Dataset>
Dimensions:      (time_agg: 2, spatial_agg: 1, timestep: 1, site: 3,
                  time: 23561, source: 1)
Coordinates:
  * time_agg     (time_agg) object 'nanmean' 'nansum'
  * spatial_agg  (spatial_agg) object 'point'
  * timestep     (timestep) object 'D'
  * site         (site) <U8 'Montreal' 'New York' 'Miami'
  * time         (time) datetime64[ns] 1959-01-01 1959-01-02 ... 2023-07-04
    latitude     (site) float64 45.5 40.75 25.75
    longitude    (site) float64 -73.5 -74.0 -80.25
  * source       (source) <U29 'era5_reanalysis_single_levels'
Data variables:
    t2m          (time_agg, spatial_agg, timestep, time, site, source) float32 ...
    tp           (time_agg, spatial_agg, timestep, time, site, source) float32 ...
Attributes: (12/30)
    GRIB_NV:                                  0
    GRIB_Nx:                                  1440
    GRIB_Ny:                                  721
    GRIB_cfName:                              unknown
    GRIB_cfVarName:                           t2m
    GRIB_dataType:                            an
    ...                                       ...
    GRIB_totalNumber:                         0
    GRIB_typeOfLevel:                         surface
    GRIB_units:                               K
    long_name:                                2 metre temperature
    standard_name:                            unknown
    units:                                    K

In [6]:
title = f"Comparison of total precipitation across three cities in North America from \
{xds.data.time.dt.year.min().values} to {xds.data.time.dt.year.max().values}"

xds.data.sel(
    timestep="D",
    spatial_agg="point",
    time_agg="nansum",
    source="era5_reanalysis_single_levels",
).hvplot(
    title=title,
    x="time",
    y="tp",
    grid=True,
    width=750,
    height=450,
    by="site",
    legend="top",
    widget_location="bottom",
)

HoloViews(NdOverlay, height=450, sizing_mode='fixed', widget_location='bottom', width=750)

In [7]:
title = f"Comparison of 2m temperature across three cities in North America from \
{xds.data.time.dt.year.min().values} to {xds.data.time.dt.year.max().values}"

xds.data.sel(
    timestep="D",
    spatial_agg="point",
    time_agg="nanmean",
    source="era5_reanalysis_single_levels",
).hvplot(
    title=title,
    x="time",
    y="t2m",
    grid=True,
    width=750,
    height=450,
    by="site",
    legend="top",
    widget_location="bottom",
)

HoloViews(NdOverlay, height=450, sizing_mode='fixed', widget_location='bottom', width=750)

### Clip on polygons with no averaging in space

Let's first access certain polygon features, which can be in the form of shapefiles, geojson, or any other format compatible with `geopandas`. In this example, we are using `JSON` (geojson) files.

In [8]:
bucket = Path("https://s3.us-east-2.wasabisys.com/watersheds-polygons/MELCC/json")

paths = [
    bucket.joinpath("023003/023003.json"),
    bucket.joinpath("031101/031101.json"),
    bucket.joinpath("040111/040111.json"),
]

Subsequently, all of the files can be opened and consolidated into a single `geopandas.GeoDataFrame` object.

In [9]:
gdf = pd.concat([gpd.read_file(path) for path in paths]).reset_index(drop=True)
gdf

Station         Superficie  \
0  023003  208.4591919813271   
1  031101  111.7131058782722   
2  040111   433.440893903503   

                                            geometry  
0  POLYGON ((-70.82601 46.81658, -70.82728 46.815...  
1  POLYGON ((-73.98519 45.21072, -73.98795 45.209...  
2  POLYGON ((-74.06645 46.02253, -74.06647 46.022...

Let's examine the geographic locations of the polygon features.

In [10]:
gdf.hvplot(
    geo=True,
    tiles="ESRI",
    color="Station",
    alpha=0.8,
    width=750,
    height=450,
    legend="top",
    hover_cols=["Station", "Superficie"],
)

:Overlay
   .WMTS.I     :WMTS   [Longitude,Latitude]
   .Polygons.I :Polygons   [Longitude,Latitude]   (Station,Superficie)

The following query seeks the variables `t2m` and `tp` from the `era5_reanalysis_single_levels` dataset, covering the period between January 1, 1959, and September 30, 1961, for the three polygons mentioned earlier. It is important to note that as `aggregation` is set to `False`, no spatial averaging will be conducted, and a mask (raster) will be returned for each polygon.

In [11]:
# FIXME: New dimensions ('lat', 'bnds') must be a superset of existing dimensions ('lat', 'bnd')

# query = {
#     "datasets": {"era5_reanalysis_single_levels": {"variables": ["t2m", "tp"]}},
#     "space": {
#         "clip": "polygon",  # bbox, point or polygon
#         "averaging": False,  # spatial average of the variables within each polygon
#         "geometry": gdf,
#         "unique_id": "Station",  # unique column name in geodataframe
#     },
#     "time": {
#         "start": "1959-01-01",
#         "end": "1963-08-31",
#     },
# }
#
# xds = xd.Query(**query)

By accessing the `data` attribute, you can view the data obtained from the query. For each variable, the dimensions of `time`, `latitude`, `longitude`, and `Station` (the unique ID) are included. In addition, there is another variable called `weights` that is returned. This variable specifies the weight that should be assigned to each pixel if spatial averaging is conducted over a mask (polygon).

In [12]:
# xds.data

Weights are much easier to comprehend visually, so let's examine the weights returned for the station *023003*. Notice that when selecting a single feature (Station *023003* in this case), the shape of our spatial dimensions is reduced to a 2x2 pixel area (longitude x latitude) that encompasses the entire feature.

In [13]:
# station = "023003"
#
# ds_station = xds.data.sel(Station=station)
# ds_clipped = xds.bbox_clip(ds_station).squeeze()
# ds_clipped

In [14]:
# FIXME: This cell raises `Exception: An axis may only be assigned one projection type`

# (
#     (
#         ds_clipped.t2m.isel(time=0).hvplot(
#             title="The 2m temperature for pixels that intersect with the polygon on January 1, 1959",
#             tiles="ESRI",
#             geo=True,
#             alpha=0.6,
#             colormap="isolum",
#             width=750,
#             height=450,
#         )
#         * gdf[gdf.Station == station].hvplot(
#             geo=True,
#             width=750,
#             height=450,
#             legend="top",
#             hover_cols=["Station", "Superficie"],
#         )
#     )
#     + ds_clipped.weights.hvplot(
#         title="The weights that should be assigned to each pixel when performing spatial averaging",
#         tiles="ESRI",
#         alpha=0.6,
#         colormap="isolum",
#         geo=True,
#         width=750,
#         height=450,
#     )
#     * gdf[gdf.Station == station].hvplot(
#         geo=True,
#         width=750,
#         height=450,
#         legend="top",
#         hover_cols=["Station", "Superficie"],
#     )
# ).cols(1)

The two plots depicted above show the 2m temperature for each pixel that intersects with the polygon from Station `023003` and the corresponding weights to be applied to each pixel. In the lower plot, it is apparent that the majority of the polygon is situated in the upper-left pixel, which results in that pixel having a weight of approximately 91%. It is evident that the two lower pixels have very minimal intersection with the polygon, which results in their respective weights being nearly zero (hover on the plot to verify the weights).

In various libraries, either all pixels that intersect with the geometries are kept, or only pixels with centers within the polygon are retained. However, as shown in the previous example, utilizing such methods can introduce significant biases in the final outcome. Indeed, keeping all four pixels intersecting with the polygon with equal weights when the temperature values in the lower pixels are roughly 2 degrees lower than that of the upper-left pixel would introduce significant biases. Therefore, utilizing weights is a more precise approach.

### Clip on polygons with averaging in space

The following query seeks the variables `t2m` and `tp` from the `era5_reanalysis_single_levels` and `era5_land_reanalysis` datasets, covering the period between January 1, 1950, to present, for the three polygons mentioned earlier. Note that when the `aggregation` parameter is set to `True`, spatial averaging takes place. In addition, the weighted mask (raster) described earlier will be applied to generate a time series for each polygon.

Additional steps are carried out in the process, including converting the original hourly time step to a daily time step. During this conversion, various temporal aggregations will be applied to each variable and a conversion to the local time zone will take place.

> **Note**
> If users prefer to pass multiple dictionaries instead of a single large one, the following format is also considered acceptable.

In [15]:
# FIXME: new dimensions ('lat', 'bnds') must be a superset of existing dimensions ('lat', 'bnd')

# datasets = {
#     "era5_reanalysis_single_levels": {"variables": ["t2m", "tp"]},
#     "era5_land_reanalysis_dev": {"variables": ["t2m", "tp"]},
# }
# space = {
#     "clip": "polygon",  # bbox, point or polygon
#     "averaging": True,
#     "geometry": gdf,  # 3 polygons
#     "unique_id": "Station",
# }
# time = {
#     "timestep": "D",
#     "aggregation": {"tp": [np.nansum], "t2m": [np.nanmax, np.nanmin]},
#     "start": "1950-01-01",
#     "timezone": "America/Montreal",
# }
#
# xds = xd.Query(datasets=datasets, space=space, time=time)

In [16]:
# xds.data

In [17]:
# FIXME: squeeze() does not work on xds.data -> list.

# xds.data.squeeze().t2m.hvplot(
#     x="time",
#     by="time_agg",
#     groupby=["source", "Station"],
#     width=750,
#     height=400,
#     grid=True,
#     widget_location="bottom",
# )

The resulting dataset can be explored in the data attribute :

In [18]:
# FIXME: squeeze() does not work on xds.data -> list.

# xds.data.squeeze().tp.sel(time_agg="nansum").hvplot(
#     x="time",
#     groupby=["source", "Station"],
#     width=750,
#     height=400,
#     color="blue",
#     grid=True,
#     widget_location="bottom",
# )

### Bounding box (bbox) around polygons

The following query seeks the variable `tp` from the `era5_land_reanalysis_dev` dataset, covering the period between January 1, 1959, and December 31, 1970, for the bounding box that delimits the three polygons mentioned earlier.

Additional steps are carried out in the process, including converting to the local time zone.

In [19]:
query = {
    "datasets": {"era5_land_reanalysis_dev": {"variables": ["tp"]}},
    "space": {
        "clip": "bbox",  # bbox, point or polygon
        "geometry": gdf,
    },
    "time": {
        "start": "1959-01-01",
        "end": "1970-12-31",
        "timezone": "America/Montreal",
    },
}


xds = xd.Query(**query)

/home/runner/micromamba/envs/xdatasets/lib/python3.9/site-packages/dask/array/core.py:4836: PerformanceWarning: Increasing number of chunks by factor of 20
  result = blockwise(
/home/runner/micromamba/envs/xdatasets/lib/python3.9/site-packages/dask/array/core.py:4836: PerformanceWarning: Increasing number of chunks by factor of 168
  result = blockwise(
/home/runner/micromamba/envs/xdatasets/lib/python3.9/site-packages/dask/array/core.py:4836: PerformanceWarning: Increasing number of chunks by factor of 18
  result = blockwise(
/home/runner/micromamba/envs/xdatasets/lib/python3.9/site-packages/dask/array/core.py:4836: PerformanceWarning: Increasing number of chunks by factor of 168
  result = blockwise(


/home/runner/micromamba/envs/xdatasets/lib/python3.9/site-packages/dask/array/core.py:4836: PerformanceWarning: Increasing number of chunks by factor of 18
  result = blockwise(
/home/runner/micromamba/envs/xdatasets/lib/python3.9/site-packages/dask/array/core.py:4836: PerformanceWarning: Increasing number of chunks by factor of 168
  result = blockwise(
/home/runner/micromamba/envs/xdatasets/lib/python3.9/site-packages/dask/array/core.py:4836: PerformanceWarning: Increasing number of chunks by factor of 18
  result = blockwise(
/home/runner/micromamba/envs/xdatasets/lib/python3.9/site-packages/dask/array/core.py:4836: PerformanceWarning: Increasing number of chunks by factor of 168
  result = blockwise(


/home/runner/micromamba/envs/xdatasets/lib/python3.9/site-packages/dask/array/core.py:4836: PerformanceWarning: Increasing number of chunks by factor of 18
  result = blockwise(
/home/runner/micromamba/envs/xdatasets/lib/python3.9/site-packages/dask/array/core.py:4836: PerformanceWarning: Increasing number of chunks by factor of 168
  result = blockwise(
/home/runner/micromamba/envs/xdatasets/lib/python3.9/site-packages/dask/array/core.py:4836: PerformanceWarning: Increasing number of chunks by factor of 19
  result = blockwise(
/home/runner/micromamba/envs/xdatasets/lib/python3.9/site-packages/dask/array/core.py:4836: PerformanceWarning: Increasing number of chunks by factor of 168
  result = blockwise(
/home/runner/work/xdatasets/xdatasets/xdatasets/workflows.py:50: UserWarning: "start_date" not found within input date time range. Defaulting to minimum time step in xarray object.
  ds = subset_time(ds, start_date=start_time, end_date=end_time)
/home/runner/work/xdatasets/xdatasets/xd

In [20]:
# FIXME: This query does not return TP - instead returns d2m, sf, sp, ssrd, strd, u10, v10

xds.data

<xarray.Dataset>
Dimensions:    (latitude: 30, longitude: 44, time: 36000, source: 1)
Coordinates:
  * latitude   (latitude) float64 47.8 47.7 47.6 47.5 ... 45.2 45.1 45.0 44.9
  * longitude  (longitude) float64 -74.9 -74.8 -74.7 -74.6 ... -70.8 -70.7 -70.6
  * time       (time) datetime64[ns] 1949-12-31T19:00:00 ... 1954-02-08T18:00:00
  * source     (source) <U24 'era5_land_reanalysis_dev'
Data variables:
    d2m        (time, latitude, longitude, source) float32 nan nan ... nan nan
    sf         (time, latitude, longitude, source) float32 nan nan ... nan nan
    sp         (time, latitude, longitude, source) float32 nan nan ... nan nan
    ssrd       (time, latitude, longitude, source) float32 nan nan ... nan nan
    strd       (time, latitude, longitude, source) float32 nan nan ... nan nan
    u10        (time, latitude, longitude, source) float32 nan nan ... 1.196
    v10        (time, latitude, longitude, source) float32 nan nan ... nan nan
Attributes:
    pangeo-forge:inputs_hash:  86f4d2953343ed66f16f2bbb8529c43ebfefe825ad6de0...
    pangeo-forge:recipe_hash:  b090aa6e3b29cd8800b0b0fa94802fb54ae1cef8d13f74...
    pangeo-forge:version:      0.9.4
    timezone:                  America/Montreal

Let's find out which day (24-hour period) was the rainiest in the entire region for the data retrieved in previous cell.

In [21]:
# indexer = (
#     xds.data.sel(source="era5_land_reanalysis_dev")
#     .tp.sum(["latitude", "longitude"])
#     .rolling(time=24)
#     .sum()
#     .argmax("time")
#     .values
# )

# xds.data.isel(time=indexer).time.dt.date.values.tolist()

Let's visualise the evolution of the hourly precipitation during that day. Note that each image (raster) delimits exactly the bounding box required to cover all polygons in the query. Please note that for full interactivity, running the code in a Jupyter Notebook is necessary.



In [22]:
# da = xds.data.tp.isel(time=slice(indexer - 24, indexer))
# # da = da.where(da>0.0001, drop=True)

# (da * 1000).sel(source="era5_land_reanalysis_dev").squeeze().hvplot.quadmesh(
#     width=750,
#     height=450,
#     geo=True,
#     tiles="ESRI",
#     groupby=["time"],
#     legend="top",
#     cmap="gist_ncar",
#     widget_location="bottom",
#     widget_type="scrubber",
#     dynamic=False,
#     clim=(0.01, 10),
# )

## Query hydrological datasets
Hydrological queries are still being tested and output format is likely to change. Stay tuned!

In [23]:
# FIXME: MELCC not yet supported.

# query = {"datasets": "melcc"}
# xds = xd.Query(**query)
# xds.data

In [24]:
query = {"datasets": "hydat"}
xds = xd.Query(**query)
xds.data

<xarray.Dataset>
Dimensions:        (data_type: 2, id: 7881, spatial_agg: 2, timestep: 1,
                    time_agg: 1, latitude: 2800, longitude: 4680, time: 59413)
Coordinates: (12/15)
  * data_type      (data_type) <U5 'flow' 'level'
    drainage_area  (id) float64 dask.array<chunksize=(10,), meta=np.ndarray>
    end_date       (id, data_type, spatial_agg, timestep, time_agg) object dask.array<chunksize=(7881, 2, 2, 1, 1), meta=np.ndarray>
  * id             (id) <U7 '01AA002' '01AD001' ... '11AF004' '11AF005'
  * latitude       (latitude) float64 85.0 84.97 84.95 ... 15.07 15.05 15.02
  * longitude      (longitude) float64 -167.0 -167.0 -166.9 ... -50.05 -50.02
    ...             ...
    source         (id) object dask.array<chunksize=(7881,), meta=np.ndarray>
  * spatial_agg    (spatial_agg) object 'point' 'watershed'
    start_date     (id, data_type, spatial_agg, timestep, time_agg) object dask.array<chunksize=(7881, 2, 2, 1, 1), meta=np.ndarray>
  * time           (time) datetime64[ns] 1860-01-01 1860-01-02 ... 2022-08-31
  * time_agg       (time_agg) <U4 'mean'
  * timestep       (timestep) <U3 'day'
Data variables:
    mask           (id, latitude, longitude) float64 dask.array<chunksize=(1, 500, 500), meta=np.ndarray>
    value          (id, time, data_type, spatial_agg, timestep, time_agg) float64 dask.array<chunksize=(10, 59413, 1, 1, 1, 1), meta=np.ndarray>

In [25]:
# FIXME: No such keys found for query

# query = {
#     "datasets": {
#         "hydrometric": {
#             "variables": ["streamflow", "t2m_nanmax", "t2m_nanmin", "tp_nansum"],
#             "id": ["01010070", "01016500", "01017290", "02*"],
#         }
#     },
# }
# xds = xd.Query(**query)
# ds_hydro = xds.data

In [26]:
# ds_hydro

In [27]:
# import panel as pn

# id1 = pn.widgets.Select(value="01010070", options=list(xds.data.id.values), name="id")
# source = pn.widgets.Select(
#     value="hydrometric", options=list(xds.data.source.values), name="source"
# )


# @pn.depends(id1, source)
# def plot_hydrograph_and_weather(id1, source):
#     da = ds_hydro.sel(id=id1, source=source)
#     dx = da["streamflow"].dropna("time", how="any")

#     trace1 = da["streamflow"].hvplot(
#         grid=True,
#         widget_location="bottom",
#         color="black",
#         xlim=(dx.time[0].values, dx.time[-1].values),
#         title=f"Daily streamflow at location {id1}",
#         width=750,
#         height=300,
#     )
#     trace2 = da[["t2m_nanmax", "t2m_nanmin"]].hvplot(
#         grid=True,
#         widget_location="bottom",
#         color=["red", "blue"],
#         xlim=(dx.time[0].values, dx.time[-1].values),
#         title=f"Daily minimum and maximum temperature at location {id1}",
#         width=750,
#         height=300,
#     )

#     trace3 = da[["tp_nansum"]].hvplot(
#         grid=True,
#         color=["turquoise"],
#         xlim=(dx.time[0].values, dx.time[-1].values),
#         title=f"Daily precipitation at location {id1}",
#         width=750,
#         height=300,
#     )

#     return pn.Column(trace1, trace2, trace3)


# pn.Row(
#     pn.Column("## Hydrometric Data Explorer", id1, source, plot_hydrograph_and_weather)
# )